## Basic GAN for a quadratic function

In [1]:
import numpy as np
import tensorflow as tf



def sample_Z(m, n):
    return np.random.uniform(-1., 1., size=[m, n]);

def get_y(x):
    
    return 10 + x*x;

def sample_data(n=1000, scale=100):
    
    data=[];
    
    x=scale*(np.random.random_sample((n,))-0.5);
    
    for i in range(n):
        
        yi = get_y(x[i]);
        data.append([x[i], yi]);
        
    return np.array(data);

# Z = placeholder for random samples Z
# array hsize for the number of hidden units in the 2 hidden layers
# reuse varibale to reuse the same hidden layers
def generator(Z, hsize=[16,16],reuse=False):
    
    with tf.variable_scope("GAN/Generator",reuse=reuse):
        
        h1 = tf.layers.dense(Z,hsize[0], activation=tf.nn.leaky_relu);
        h2 = tf.layers.dense(h1,hsize[1],activation=tf.nn.leaky_relu);
        
        out = tf.layers.dense(h2,2);
    return out;

# X - This function takes input placeholder for the samples from the vector space of real dataset
# We use 3 hidden layers for the Discriminator out of which first 2 layers size we take input.
# We fix the size of the third hidden layer to 2 so that we can visualize the transformed feature space in a 2D plane.
# The output of this function is a logit prediction for the given X 
# and the output of the last layer which is the feature transformation learned by Discriminator for X. 
# The logit function is the inverse of the sigmoid function which is used to represent 
# the logarithm of the odds (ratio of the probability of variable being 1 to that of it being 0).

def discriminator(X,hsize=[16, 16],reuse=False):
    with tf.variable_scope("GAN/Discriminator",reuse=reuse):
        h1 = tf.layers.dense(X,hsize[0],activation=tf.nn.leaky_relu);
        h2 = tf.layers.dense(h1,hsize[1],activation=tf.nn.leaky_relu);
        h3 = tf.layers.dense(h2,2);
        out = tf.layers.dense(h3,1);

    return out, h3;


# for training, we define the following placeholders for real samples and random noise samples.
X = tf.placeholder(tf.float32,[None,2]);
Z = tf.placeholder(tf.float32,[None,2]);

# We also need to create the graph for generating samples from Generator network 
# and feeding real and generated samples to the Discriminator network. 
G_sample = generator(Z);
r_logits, r_rep = discriminator(X);
f_logits, g_rep = discriminator(G_sample,reuse=True);


# Using the logits for generated data and real data we define the loss functions for the Generator and Discriminator networks
# These losses are sigmoid cross entropy based losses using the equations we defined above. This is a commonly used loss function for so-called discrete classification. 
# It takes as input the logit (which is given by our discriminator network) and true labels for each sample.
# It then calculates the error for each sample.
disc_loss = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=r_logits,labels=tf.ones_like(r_logits)) + tf.nn.sigmoid_cross_entropy_with_logits(logits=f_logits,labels=tf.zeros_like(f_logits)));  
gen_loss = tf.reduce_mean(tf.nn.sigmoid_cross_entropy_with_logits(logits=f_logits,labels=tf.ones_like(f_logits)));


# Next, we define the optimizers for the two networks using the loss functions defined above 
# and scope of the layers defined in the generator and discriminator functions. 
# We use RMSProp Optimizer for both the networks with the learning rate as 0.001.
# Using the scope we fetch the weights/variables for the given network only.
gen_vars = tf.get_collection(tf.GraphKeys.GLOBAL_VARIABLES,scope="GAN/Generator");
disc_vars = tf.get_collection(tf.GraphKeys.GLOBAL_VARIABLES,scope="GAN/Discriminator");

gen_step = tf.train.RMSPropOptimizer(learning_rate=0.001).minimize(gen_loss,var_list = gen_vars); 
disc_step = tf.train.RMSPropOptimizer(learning_rate=0.001).minimize(disc_loss,var_list = disc_vars); 


sess = tf.Session();
tf.global_variables_initializer().run(session=sess);

batch_size = 256;
nd_steps = 10;
ng_steps = 10;

# We then train both the networks in an alternating way for the required number of steps:

for i in range(100001):
    X_batch = sample_data(n=batch_size)
    Z_batch = sample_Z(batch_size, 2)
    _, dloss = sess.run([disc_step, disc_loss], feed_dict={X: X_batch, Z: Z_batch})
    _, gloss = sess.run([gen_step, gen_loss], feed_dict={Z: Z_batch})

    print ("Iterations: %d\t Discriminator loss: %.4f\t Generator loss: %.4f"%(i,dloss,gloss));

Instructions for updating:
Use keras.layers.dense instead.
Instructions for updating:
Colocations handled automatically by placer.
Iterations: 0	 Discriminator loss: 0.7217	 Generator loss: 0.6692
Iterations: 1	 Discriminator loss: 0.7197	 Generator loss: 0.6703
Iterations: 2	 Discriminator loss: 0.7198	 Generator loss: 0.6702
Iterations: 3	 Discriminator loss: 0.7169	 Generator loss: 0.6731
Iterations: 4	 Discriminator loss: 0.7172	 Generator loss: 0.6732
Iterations: 5	 Discriminator loss: 0.7158	 Generator loss: 0.6743
Iterations: 6	 Discriminator loss: 0.7152	 Generator loss: 0.6749
Iterations: 7	 Discriminator loss: 0.7153	 Generator loss: 0.6749
Iterations: 8	 Discriminator loss: 0.7133	 Generator loss: 0.6767
Iterations: 9	 Discriminator loss: 0.7130	 Generator loss: 0.6767
Iterations: 10	 Discriminator loss: 0.7111	 Generator loss: 0.6788
Iterations: 11	 Discriminator loss: 0.7073	 Generator loss: 0.6826
Iterations: 12	 Discriminator loss: 0.7109	 Generator loss: 0.6783
Iteratio

Iterations: 171	 Discriminator loss: 0.2585	 Generator loss: 1.5261
Iterations: 172	 Discriminator loss: 0.2511	 Generator loss: 1.5552
Iterations: 173	 Discriminator loss: 0.2566	 Generator loss: 1.5494
Iterations: 174	 Discriminator loss: 0.2490	 Generator loss: 1.5592
Iterations: 175	 Discriminator loss: 0.2461	 Generator loss: 1.5820
Iterations: 176	 Discriminator loss: 0.2399	 Generator loss: 1.5993
Iterations: 177	 Discriminator loss: 0.2330	 Generator loss: 1.6209
Iterations: 178	 Discriminator loss: 0.2361	 Generator loss: 1.6244
Iterations: 179	 Discriminator loss: 0.2321	 Generator loss: 1.6324
Iterations: 180	 Discriminator loss: 0.2308	 Generator loss: 1.6441
Iterations: 181	 Discriminator loss: 0.2246	 Generator loss: 1.6629
Iterations: 182	 Discriminator loss: 0.2255	 Generator loss: 1.6688
Iterations: 183	 Discriminator loss: 0.2234	 Generator loss: 1.6770
Iterations: 184	 Discriminator loss: 0.2172	 Generator loss: 1.6997
Iterations: 185	 Discriminator loss: 0.2126	 Gen

Iterations: 344	 Discriminator loss: 0.0815	 Generator loss: 4.2322
Iterations: 345	 Discriminator loss: 0.0696	 Generator loss: 4.3214
Iterations: 346	 Discriminator loss: 0.1160	 Generator loss: 3.9977
Iterations: 347	 Discriminator loss: 0.0887	 Generator loss: 4.1710
Iterations: 348	 Discriminator loss: 0.0788	 Generator loss: 4.2307
Iterations: 349	 Discriminator loss: 0.0696	 Generator loss: 4.2917
Iterations: 350	 Discriminator loss: 0.1021	 Generator loss: 4.2792
Iterations: 351	 Discriminator loss: 0.0978	 Generator loss: 4.2467
Iterations: 352	 Discriminator loss: 0.0785	 Generator loss: 4.3830
Iterations: 353	 Discriminator loss: 0.1083	 Generator loss: 4.1004
Iterations: 354	 Discriminator loss: 0.0834	 Generator loss: 4.4469
Iterations: 355	 Discriminator loss: 0.0824	 Generator loss: 4.3712
Iterations: 356	 Discriminator loss: 0.1105	 Generator loss: 4.2285
Iterations: 357	 Discriminator loss: 0.1201	 Generator loss: 4.0910
Iterations: 358	 Discriminator loss: 0.1159	 Gen

Iterations: 503	 Discriminator loss: 0.3460	 Generator loss: 3.9245
Iterations: 504	 Discriminator loss: 0.4028	 Generator loss: 3.5238
Iterations: 505	 Discriminator loss: 0.3350	 Generator loss: 4.4399
Iterations: 506	 Discriminator loss: 0.5127	 Generator loss: 3.1564
Iterations: 507	 Discriminator loss: 0.3941	 Generator loss: 4.0404
Iterations: 508	 Discriminator loss: 0.4635	 Generator loss: 3.6112
Iterations: 509	 Discriminator loss: 0.3219	 Generator loss: 3.8335
Iterations: 510	 Discriminator loss: 0.3504	 Generator loss: 3.7898
Iterations: 511	 Discriminator loss: 0.3417	 Generator loss: 3.7862
Iterations: 512	 Discriminator loss: 0.4507	 Generator loss: 3.6091
Iterations: 513	 Discriminator loss: 0.3993	 Generator loss: 3.9349
Iterations: 514	 Discriminator loss: 0.4026	 Generator loss: 3.3655
Iterations: 515	 Discriminator loss: 0.3679	 Generator loss: 3.9955
Iterations: 516	 Discriminator loss: 0.3804	 Generator loss: 3.3549
Iterations: 517	 Discriminator loss: 0.3158	 Gen

Iterations: 677	 Discriminator loss: 0.6334	 Generator loss: 2.2646
Iterations: 678	 Discriminator loss: 0.6979	 Generator loss: 3.1670
Iterations: 679	 Discriminator loss: 0.7632	 Generator loss: 2.4449
Iterations: 680	 Discriminator loss: 0.6112	 Generator loss: 3.4020
Iterations: 681	 Discriminator loss: 0.6640	 Generator loss: 2.1417
Iterations: 682	 Discriminator loss: 0.4856	 Generator loss: 3.5917
Iterations: 683	 Discriminator loss: 0.7188	 Generator loss: 2.0475
Iterations: 684	 Discriminator loss: 0.6685	 Generator loss: 3.6546
Iterations: 685	 Discriminator loss: 0.7196	 Generator loss: 1.8998
Iterations: 686	 Discriminator loss: 0.8508	 Generator loss: 3.4734
Iterations: 687	 Discriminator loss: 0.6205	 Generator loss: 2.4093
Iterations: 688	 Discriminator loss: 0.6200	 Generator loss: 3.2201
Iterations: 689	 Discriminator loss: 0.6343	 Generator loss: 2.2620
Iterations: 690	 Discriminator loss: 0.7739	 Generator loss: 3.0579
Iterations: 691	 Discriminator loss: 0.7297	 Gen

...

Iterations: 99391	 Discriminator loss: 1.3865	 Generator loss: 0.6928
Iterations: 99392	 Discriminator loss: 1.3862	 Generator loss: 0.6918
Iterations: 99393	 Discriminator loss: 1.3862	 Generator loss: 0.6914
Iterations: 99394	 Discriminator loss: 1.3871	 Generator loss: 0.6950
Iterations: 99395	 Discriminator loss: 1.3863	 Generator loss: 0.6949
Iterations: 99396	 Discriminator loss: 1.3863	 Generator loss: 0.6949
Iterations: 99397	 Discriminator loss: 1.3863	 Generator loss: 0.6947
Iterations: 99398	 Discriminator loss: 1.3864	 Generator loss: 0.6931
Iterations: 99399	 Discriminator loss: 1.3862	 Generator loss: 0.6913
Iterations: 99400	 Discriminator loss: 1.3864	 Generator loss: 0.6931
Iterations: 99401	 Discriminator loss: 1.3861	 Generator loss: 0.6902
Iterations: 99402	 Discriminator loss: 1.3865	 Generator loss: 0.6941
Iterations: 99403	 Discriminator loss: 1.3861	 Generator loss: 0.6913
Iterations: 99404	 Discriminator loss: 1.3859	 Generator loss: 0.6865
Iterations: 99405	 D

Iterations: 99528	 Discriminator loss: 1.3864	 Generator loss: 0.6928
Iterations: 99529	 Discriminator loss: 1.3865	 Generator loss: 0.6949
Iterations: 99530	 Discriminator loss: 1.3864	 Generator loss: 0.6960
Iterations: 99531	 Discriminator loss: 1.3863	 Generator loss: 0.6975
Iterations: 99532	 Discriminator loss: 1.3860	 Generator loss: 0.6985
Iterations: 99533	 Discriminator loss: 1.3864	 Generator loss: 0.6938
Iterations: 99534	 Discriminator loss: 1.3863	 Generator loss: 0.6897
Iterations: 99535	 Discriminator loss: 1.3865	 Generator loss: 0.6916
Iterations: 99536	 Discriminator loss: 1.3863	 Generator loss: 0.6904
Iterations: 99537	 Discriminator loss: 1.3866	 Generator loss: 0.6948
Iterations: 99538	 Discriminator loss: 1.3865	 Generator loss: 0.6982
Iterations: 99539	 Discriminator loss: 1.3863	 Generator loss: 0.6960
Iterations: 99540	 Discriminator loss: 1.3863	 Generator loss: 0.6966
Iterations: 99541	 Discriminator loss: 1.3863	 Generator loss: 0.6991
Iterations: 99542	 D

Iterations: 99667	 Discriminator loss: 1.3860	 Generator loss: 0.7020
Iterations: 99668	 Discriminator loss: 1.3881	 Generator loss: 0.6903
Iterations: 99669	 Discriminator loss: 1.3865	 Generator loss: 0.6888
Iterations: 99670	 Discriminator loss: 1.3862	 Generator loss: 0.6874
Iterations: 99671	 Discriminator loss: 1.3863	 Generator loss: 0.6884
Iterations: 99672	 Discriminator loss: 1.3861	 Generator loss: 0.6867
Iterations: 99673	 Discriminator loss: 1.3865	 Generator loss: 0.6906
Iterations: 99674	 Discriminator loss: 1.3866	 Generator loss: 0.6926
Iterations: 99675	 Discriminator loss: 1.3863	 Generator loss: 0.6920
Iterations: 99676	 Discriminator loss: 1.3863	 Generator loss: 0.6917
Iterations: 99677	 Discriminator loss: 1.3863	 Generator loss: 0.6926
Iterations: 99678	 Discriminator loss: 1.3864	 Generator loss: 0.6924
Iterations: 99679	 Discriminator loss: 1.3863	 Generator loss: 0.6921
Iterations: 99680	 Discriminator loss: 1.3863	 Generator loss: 0.6925
Iterations: 99681	 D

Iterations: 99801	 Discriminator loss: 1.3863	 Generator loss: 0.6952
Iterations: 99802	 Discriminator loss: 1.3864	 Generator loss: 0.6928
Iterations: 99803	 Discriminator loss: 1.3863	 Generator loss: 0.6940
Iterations: 99804	 Discriminator loss: 1.3864	 Generator loss: 0.6928
Iterations: 99805	 Discriminator loss: 1.3863	 Generator loss: 0.6929
Iterations: 99806	 Discriminator loss: 1.3862	 Generator loss: 0.6920
Iterations: 99807	 Discriminator loss: 1.3869	 Generator loss: 0.6938
Iterations: 99808	 Discriminator loss: 1.3863	 Generator loss: 0.6921
Iterations: 99809	 Discriminator loss: 1.3864	 Generator loss: 0.6944
Iterations: 99810	 Discriminator loss: 1.3863	 Generator loss: 0.6935
Iterations: 99811	 Discriminator loss: 1.3864	 Generator loss: 0.6931
Iterations: 99812	 Discriminator loss: 1.3863	 Generator loss: 0.6929
Iterations: 99813	 Discriminator loss: 1.3863	 Generator loss: 0.6938
Iterations: 99814	 Discriminator loss: 1.3863	 Generator loss: 0.6931
Iterations: 99815	 D

Iterations: 99938	 Discriminator loss: 1.3863	 Generator loss: 0.6935
Iterations: 99939	 Discriminator loss: 1.3864	 Generator loss: 0.6930
Iterations: 99940	 Discriminator loss: 1.3862	 Generator loss: 0.6940
Iterations: 99941	 Discriminator loss: 1.3865	 Generator loss: 0.6918
Iterations: 99942	 Discriminator loss: 1.3863	 Generator loss: 0.6933
Iterations: 99943	 Discriminator loss: 1.3863	 Generator loss: 0.6924
Iterations: 99944	 Discriminator loss: 1.3863	 Generator loss: 0.6916
Iterations: 99945	 Discriminator loss: 1.3862	 Generator loss: 0.6872
Iterations: 99946	 Discriminator loss: 1.3859	 Generator loss: 0.6824
Iterations: 99947	 Discriminator loss: 1.3885	 Generator loss: 0.6962
Iterations: 99948	 Discriminator loss: 1.3862	 Generator loss: 0.6949
Iterations: 99949	 Discriminator loss: 1.3863	 Generator loss: 0.6945
Iterations: 99950	 Discriminator loss: 1.3863	 Generator loss: 0.6939
Iterations: 99951	 Discriminator loss: 1.3863	 Generator loss: 0.6945
Iterations: 99952	 D